In [ ]:
%matplotlib inline



#  Work with the Cognitive Atlas

We can download the Cognitive Atlas and extract CogAt terms from text.


In [ ]:
import os
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

import nimare
from nimare import annotate, extract
from nimare.tests.utils import get_test_data_path

Load dataset with abstracts
---------------------------



In [ ]:
dset = nimare.dataset.Dataset.load(
    os.path.join(get_test_data_path(), 'neurosynth_laird_studies.pkl.gz'))

Download Cognitive Atlas
------------------------



In [ ]:
cogatlas = extract.download_cognitive_atlas(
    data_dir=get_test_data_path(), overwrite=False)
id_df = pd.read_csv(cogatlas['ids'])
rel_df = pd.read_csv(cogatlas['relationships'])
print('id_df:')
print(id_df.head())
print('rel_df:')
print(rel_df.head())

Extract Cognitive Atlas terms from text
---------------------------------------



In [ ]:
counts_df, rep_text_df = annotate.cogat.extract_cogat(
    dset.texts, id_df, text_column='abstract')

Expand counts
-------------



In [ ]:
weights = {'isKindOf': 1, 'isPartOf': 1, 'inCategory': 1}
expanded_df = annotate.cogat.expand_counts(counts_df, rel_df, weights)
# Sort by total count and reduce for better visualization
series = expanded_df.sum(axis=0)
series = series.sort_values(ascending=False)
series = series[series > 0]
columns = series.index.tolist()

Make some plots
---------------
We will reduce the dataframes to only columns with at least one count to make
visualization easier.



In [ ]:
# Raw counts
fig1, ax1 = plt.subplots(figsize=(16, 8))
pos = ax1.imshow(counts_df[columns].values, aspect='auto',
                 vmin=0, vmax=np.max(expanded_df.values))
fig1.colorbar(pos, ax=ax1)
ax1.set_title('Counts Before Expansion', fontsize=20)
ax1.set_yticks(range(counts_df.shape[0]))
ax1.set_yticklabels(counts_df.index)
ax1.set_ylabel('Study', fontsize=16)
ax1.set_xticks(range(len(columns)))
ax1.set_xticklabels(columns, rotation=90)
ax1.set_xlabel('Cognitive Atlas Term', fontsize=16)
fig1.tight_layout()
fig1.show()

# Expanded counts
fig2, ax2 = plt.subplots(figsize=(16, 8))
pos = ax2.imshow(expanded_df[columns].values, aspect='auto',
                 vmin=0, vmax=np.max(expanded_df.values))
fig2.colorbar(pos, ax=ax2)
ax2.set_title('Counts After Expansion', fontsize=20)
ax2.set_yticks(range(counts_df.shape[0]))
ax2.set_yticklabels(counts_df.index)
ax2.set_ylabel('Study', fontsize=16)
ax2.set_xticks(range(len(columns)))
ax2.set_xticklabels(columns, rotation=90)
ax2.set_xlabel('Cognitive Atlas Term', fontsize=16)
fig2.tight_layout()
fig2.show()